<h1 align=center><font size = 5>Battle of Neighborhoods-Capstone Project</font></h1>

### Segmenting and Clustering Neighborhoods in New York City

In [2]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


<a id='item1'></a>

#### Load and explore the data

In [4]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [5]:
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

In [6]:
neighborhoods_data = newyork_data['features']

In [7]:
neighborhoods_data[0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

#### Tranform the data into a *pandas* dataframe

In [8]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

In [9]:
neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

Then let's loop through the data and fill the dataframe one row at a time.

In [10]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

Quickly examine the resulting dataframe.

In [11]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [17]:
neighborhoods

Borough               Neighborhood   Latitude  Longitude
0            Bronx                  Wakefield  40.894705 -73.847201
1            Bronx                 Co-op City  40.874294 -73.829939
2            Bronx                Eastchester  40.887556 -73.827806
3            Bronx                  Fieldston  40.895437 -73.905643
4            Bronx                  Riverdale  40.890834 -73.912585
5            Bronx                Kingsbridge  40.881687 -73.902818
6        Manhattan                Marble Hill  40.876551 -73.910660
7            Bronx                   Woodlawn  40.898273 -73.867315
8            Bronx                    Norwood  40.877224 -73.879391
9            Bronx             Williamsbridge  40.881039 -73.857446
10           Bronx                 Baychester  40.866858 -73.835798
11           Bronx             Pelham Parkway  40.857413 -73.854756
12           Bronx                City Island  40.847247 -73.786488
13           Bronx               Bedford Park  40.870185 -73.885512
14           Bronx         University Heights  40.855727 -73.910416
15           Bronx             Morris Heights  40.847898 -73.919672
16           Bronx                    Fordham  40.860997 -73.896427
17           Bronx               East Tremont  40.842696 -73.887356
18           Bronx                 West Farms  40.839475 -73.877745
19           Bronx               High  Bridge  40.836623 -73.926102
20           Bronx                    Melrose  40.819754 -73.909422
21           Bronx                 Mott Haven  40.806239 -73.916100
22           Bronx                Port Morris  40.801664 -73.913221
23           Bronx                   Longwood  40.815099 -73.895788
24           Bronx                Hunts Point  40.809730 -73.883315
25           Bronx                 Morrisania  40.823592 -73.901506
26           Bronx                  Soundview  40.821012 -73.865746
27           Bronx               Clason Point  40.806551 -73.854144
28           Bronx                Throgs Neck  40.815109 -73.816350
29           Bronx               Country Club  40.844246 -73.824099
30           Bronx                Parkchester  40.837938 -73.856003
31           Bronx         Westchester Square  40.840619 -73.842194
32           Bronx                   Van Nest  40.843608 -73.866299
33           Bronx                Morris Park  40.847549 -73.850402
34           Bronx                    Belmont  40.857277 -73.888452
35           Bronx             Spuyten Duyvil  40.881395 -73.917190
36           Bronx            North Riverdale  40.908543 -73.904531
37           Bronx                 Pelham Bay  40.850641 -73.832074
38           Bronx              Schuylerville  40.826580 -73.826203
39           Bronx             Edgewater Park  40.821986 -73.813885
40           Bronx                Castle Hill  40.819014 -73.848027
41           Bronx                  Olinville  40.871371 -73.863324
42           Bronx             Pelham Gardens  40.862966 -73.841612
43           Bronx                  Concourse  40.834284 -73.915589
44           Bronx                  Unionport  40.829774 -73.850535
45           Bronx                   Edenwald  40.884561 -73.848083
46        Brooklyn                  Bay Ridge  40.625801 -74.030621
47        Brooklyn                Bensonhurst  40.611009 -73.995180
48        Brooklyn                Sunset Park  40.645103 -74.010316
49        Brooklyn                 Greenpoint  40.730201 -73.954241
50        Brooklyn                  Gravesend  40.595260 -73.973471
51        Brooklyn             Brighton Beach  40.576825 -73.965094
52        Brooklyn             Sheepshead Bay  40.586890 -73.943186
53        Brooklyn          Manhattan Terrace  40.614433 -73.957438
54        Brooklyn                   Flatbush  40.636326 -73.958401
55        Brooklyn              Crown Heights  40.670829 -73.943291
56        Brooklyn              East Flatbush  40.641718 -73.936103
57        Brooklyn                 Kensington  40.642382 -73.980421

And make sure that the dataset has all 5 boroughs and 306 neighborhoods.

In [12]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


#### Use geopy library to get the latitude and longitude values of New York City.

In order to define an instance of the geocoder, we need to define a user_agent. We will name our agent <em>ny_explorer</em>, as shown below.

In [13]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


#### Create a map of New York with neighborhoods superimposed on top.

In [16]:
manhattan_data = neighborhoods[neighborhoods['Borough'] == 'Manhattan'].reset_index(drop=True)
manhattan_data.head()

Borough        Neighborhood   Latitude  Longitude
0  Manhattan         Marble Hill  40.876551 -73.910660
1  Manhattan           Chinatown  40.715618 -73.994279
2  Manhattan  Washington Heights  40.851903 -73.936900
3  Manhattan              Inwood  40.867684 -73.921210
4  Manhattan    Hamilton Heights  40.823604 -73.949688

Let's get the geographical coordinates of Manhattan.

In [17]:
address = 'Manhattan, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Manhattan are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Manhattan are 40.7896239, -73.9598939.


As we did with all of New York City, let's visualizat Manhattan the neighborhoods in it.

Next, we are going to start utilizing the Foursquare API to explore the neighborhoods and segment them.

#### Define Foursquare Credentials and Version

In [15]:
CLIENT_ID = 'your-client-ID' # your Foursquare ID
CLIENT_ID = '3LAJCUZ51JM5TNVOLIT5MNHR3H2ESX3H1H5E4W00EAJFT0PV' # your Foursquare ID

CLIENT_SECRET = 'your-client-secret' # your Foursquare Secret
CLIENT_SECRET = 'VES3FVJWFHHMSJDRIYIG4BZWT1SVUGX3VD5RJJPSNLBQQWQQ' # your Foursquare Secret

VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 3LAJCUZ51JM5TNVOLIT5MNHR3H2ESX3H1H5E4W00EAJFT0PV
CLIENT_SECRET:VES3FVJWFHHMSJDRIYIG4BZWT1SVUGX3VD5RJJPSNLBQQWQQ


#### Now, let's get the top 100 venues that are in New York within a radius of 500 meters.

First, let's create the GET request URL. Name your URL **url**.

In [ ]:
radius = 200

In [22]:
# type your answer here
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            200, 
            10)
url



'https://api.foursquare.com/v2/venues/explore?&client_id=3LAJCUZ51JM5TNVOLIT5MNHR3H2ESX3H1H5E4W00EAJFT0PV&client_secret=VES3FVJWFHHMSJDRIYIG4BZWT1SVUGX3VD5RJJPSNLBQQWQQ&v=20180605&ll=40.75665808227519,-74.00011136202637&radius=200&limit=10'

Send the GET request and examine the resutls

In [23]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5e1e260d216785001b4fa14b'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'},
    {'name': '$-$$$$', 'key': 'price'}]},
  'headerLocation': "Hell's Kitchen",
  'headerFullLocation': "Hell's Kitchen, New York",
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 14,
  'suggestedBounds': {'ne': {'lat': 40.75845808407519,
    'lng': -73.9977395246873},
   'sw': {'lat': 40.75485808047519, 'lng': -74.00248319936544}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '55d12634498ee6d387a520a5',
       'name': 'Bella Abzug Park',
       'location': {'address': 'Hudson Blvd',
        'crossStreet': 'at 11th Ave',
        'lat': 40.75557964275589,
        'lng': -74.0

From the Foursquare lab in the previous module, we know that all the information is in the *items* key. Before we proceed, let's borrow the **get_category_type** function from the Foursquare lab.

In [24]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

Now we are ready to clean the json and structure it into a *pandas* dataframe.

In [25]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name                                categories        lat  \
0     Bella Abzug Park                                      Park  40.755580   
1               505W37  Residential Building (Apartment / Condo)  40.756909   
2       Legacy Records                       American Restaurant  40.757565   
3   Sean Kelly Gallery                               Art Gallery  40.756022   
4  Manhattan Aquariums                                 Pet Store  40.757029   

         lng  
0 -74.000344  
1 -73.998007  
2 -73.998111  
3 -73.998306  
4 -73.999085

And how many venues were returned by Foursquare?

In [26]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

10 venues were returned by Foursquare.


<a id='item2'></a>

## 2. Explore Neighborhoods in Manhattan

#### Let's create a function to repeat the same process to all the neighborhoods in Manhattan

In [100]:
radius = 200
LIMIT  = 1000

In [101]:
def getNearbyVenues(names, latitudes, longitudes, radius=200):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

#### Now write the code to run the above function on each neighborhood and create a new dataframe called *manhattan_venues*.

In [102]:
# type your answer here

NY_venues = getNearbyVenues(names=neighborhoods['Neighborhood'],
                                   latitudes=neighborhoods['Latitude'],
                                   longitudes=neighborhoods['Longitude']
                                   )



Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

#### Let's check the size of the resulting dataframe

In [105]:
print(NY_venues.shape)
NY_venues.head()

(2720, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4   Co-op City              40.874294              -73.829939   

                                            Venue  Venue Latitude  \
0                                Lollipops Gelato       40.894123   
1                                           Shell       40.894187   
2  Shepherd ENG Heating Cooling And Refrigeration       40.895539   
3                                     Pitman Deli       40.894149   
4                         Modell's Sporting Goods       40.872584   

   Venue Longitude              Venue Category  
0       -73.845892                Dessert Shop  
1       -73.845862                 Gas Station  
2       -73.848241  Construction & Landscaping  
3       -73.845748                        Food  
4       -73.829532         Sporting Goods Shop

Let's check how many venues were returned for each neighborhood

In [144]:
NY_venues.groupby('Neighborhood').count()


Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Allerton                                      11                      11   
Annadale                                       1                       1   
Arden Heights                                  1                       1   
Arlington                                      2                       2   
Arrochar                                       2                       2   
Astoria                                        3                       3   
Astoria Heights                                5                       5   
Auburndale                                     3                       3   
Bath Beach                                     4                       4   
Battery Park City                             28                      28   
Bay Ridge                                     19                      19   
Bay Terrace                                    9                       9   
Baychester                                     2                       2   
Bayside                                        8                       8   
Bedford Park                                   2                       2   
Beechhurst                                     3                       3   
Bellaire                                       3                       3   
Belle Harbor                                   2                       2   
Bellerose                                      3                       3   
Belmont                                        7                       7   
Bensonhurst                                    1                       1   
Blissville                                     1                       1   
Boerum Hill                                   14                      14   
Brighton Beach                                17                      17   
Broad Channel                                  3                       3   
Broadway Junction                              7                       7   
Bronxdale                                      1                       1   
Brooklyn Heights                              41                      41   
Brookville                                     1                       1   
Brownsville                                    5                       5   
Bulls Head                                     2                       2   
Bushwick                                      13                      13   
Butler Manor                                   2                       2   
Cambria Heights                                7                       7   
Canarsie                                       1                       1   
Carnegie Hill                                 21                      21   
Carroll Gardens                               37                      37   
Castle Hill                                    2                       2   
Castleton Corners                              4                       4   
Central Harlem                                15                      15   
Charleston                                     8                       8   
Chelsea                                       21                      21   
Chinatown                                     17                      17   
City Island                                   13                      13   
City Line                                     12                      12   
Civic Center                                  31                      31   
Claremont Village                              5                       5   
Clason Point                                   6                       6   
Clinton                                       35                      35   
Clinton Hill                                  26                      26   
Co-op City                                     3                       3   

#### Let's find out how many unique categories can be curated from all the returned venues

In [107]:
print('There are {} uniques categories.'.format(len(NY_venues['Venue Category'].unique())))

There are 313 uniques categories.


<a id='item3'></a>

## 3. Analyze Each Neighborhood

In [108]:
# one hot encoding
NY_onehot = pd.get_dummies(NY_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
NY_onehot['Neighborhood'] = NY_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [NY_onehot.columns[-1]] + list(NY_onehot.columns[:-1])
NY_onehot = NY_onehot[fixed_columns]

NY_onehot.head()

Yoga Studio  Accessories Store  Adult Boutique  Afghan Restaurant  \
0            0                  0               0                  0   
1            0                  0               0                  0   
2            0                  0               0                  0   
3            0                  0               0                  0   
4            0                  0               0                  0   

   American Restaurant  Animal Shelter  Antique Shop  Arcade  \
0                    0               0             0       0   
1                    0               0             0       0   
2                    0               0             0       0   
3                    0               0             0       0   
4                    0               0             0       0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Asian Restaurant  Automotive Shop  BBQ Joint  Bagel Shop  Bakery  Bank  \
0                 0                0          0           0       0     0   
1                 0                0          0           0       0     0   
2                 0                0          0           0       0     0   
3                 0                0          0           0       0     0   
4                 0                0          0           0       0     0   

   Bar  Baseball Field  Basketball Court  Beach  Beer Bar  Beer Garden  \
0    0               0                 0      0         0            0   
1    0               0                 0      0         0            0   
2    0               0                 0      0         0            0   
3    0               0                 0      0         0            0   
4    0               0                 0      0         0            0   

   Beer Store  Big Box Store  Bike Rental / Bike Share  Bike Shop  Bistro  \
0           0              0                         0          0       0   
1           0              0                         0          0       0   
2           0              0                         0          0       0   
3           0              0                         0          0       0   
4           0              0                         0          0       0   

   Board Shop  Boat or Ferry  Bookstore  Boutique  Bowling Alley  Boxing Gym  \
0           0              0          0         0              0           0   
1           0              0          0         0              0           0   
2           0              0          0         0              0           0   
3           0              0          0         0              0           0   
4           0              0          0         0              0           0   

   Breakfast Spot  Brewery  Bridal Shop  Bubble Tea Shop  Building  \
0               0        0            0                0         0   
1               0        0            0                0         0   
2               0        0            0                0         0   
3               0        0            0                0         0   
4               0        0            0                0         0   

   Burger Joint  Burrito Place  Bus Line  Bus Station  Bus Stop  \
0             0              0         0            0         0   
1             0              0         0            0         0   
2             0              0         0            0         0   
3             0              0         0            0         0   
4             0              0         0            0         0   

   Business Service  Butcher  Café  Cajun / Creole Restaur

And let's examine the new dataframe size.

In [109]:
NY_onehot.shape

(2720, 313)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [110]:
NY_grouped = NY_onehot.groupby('Neighborhood').mean().reset_index()
NY_grouped

Neighborhood  Yoga Studio  Accessories Store  \
0                     Allerton     0.000000           0.000000   
1                     Annadale     0.000000           0.000000   
2                Arden Heights     0.000000           0.000000   
3                    Arlington     0.000000           0.000000   
4                     Arrochar     0.000000           0.000000   
5                      Astoria     0.000000           0.000000   
6              Astoria Heights     0.000000           0.000000   
7                   Auburndale     0.000000           0.000000   
8                   Bath Beach     0.000000           0.000000   
9            Battery Park City     0.000000           0.000000   
10                   Bay Ridge     0.000000           0.000000   
11                 Bay Terrace     0.000000           0.000000   
12                  Baychester     0.000000           0.000000   
13                     Bayside     0.000000           0.000000   
14                Bedford Park     0.000000           0.000000   
15                  Beechhurst     0.000000           0.000000   
16                    Bellaire     0.000000           0.000000   
17                Belle Harbor     0.000000           0.000000   
18                   Bellerose     0.000000           0.000000   
19                     Belmont     0.000000           0.000000   
20                 Bensonhurst     0.000000           0.000000   
21                  Blissville     0.000000           0.000000   
22                 Boerum Hill     0.000000           0.000000   
23              Brighton Beach     0.000000           0.000000   
24               Broad Channel     0.000000           0.000000   
25           Broadway Junction     0.000000           0.000000   
26                   Bronxdale     0.000000           0.000000   
27            Brooklyn Heights     0.073171           0.000000   
28                  Brookville     0.000000           0.000000   
29                 Brownsville     0.000000           0.000000   
30                  Bulls Head     0.000000           0.000000   
31                    Bushwick     0.000000           0.000000   
32                Butler Manor     0.000000           0.000000   
33             Cambria Heights     0.000000           0.000000   
34                    Canarsie     0.000000           0.000000   
35               Carnegie Hill     0.000000           0.000000   
36             Carroll Gardens     0.000000           0.000000   
37                 Castle Hill     0.000000           0.000000   
38           Castleton Corners     0.000000           0.000000   
39              Central Harlem     0.000000           0.000000   
40                  Charleston     0.000000           0.000000   
41                     Chelsea     0.000000           0.000000   
42                   Chinatown     0.000000           0.000000   
43                 City Island     0.000000           0.000000   
44                   City Line     0.000000           0.000000   
45                Civic Center     0.000000           0.000000   
46           Claremont Village     0.000000           0.000000   
47                Clason Point     0.000000           0.000000   
48                     Clinton     0.000000           0.000000   
49                Clinton Hill     0.038462           0.000000   
50                  Co-op City     0.000000           0.000000   
51                 Cobble Hill     0.000000           0.000000   
52               College Point     0.000000           0.000000   
53                     Concord     0.000000           0.000000   
54                   Concourse     0.000000           0.000000   
55           Concourse Village     0.000000           0.000000   
56                Coney Island     0.000000           0.000000   
57                      Corona     0.000000           0.000000   
58               Crown Heights     0.000000           0.000000   
59               Cypress Hills     0.000000           0.00

#### Let's confirm the new size

In [111]:
NY_grouped.shape

(255, 313)

#### Let's print each neighborhood along with the top 5 most common venues

In [134]:
num_top_venues = 20


for hood in NY_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = NY_grouped[NY_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Allerton----
                      venue  freq
0               Pizza Place  0.18
1             Deli / Bodega  0.09
2                Donut Shop  0.09
3               Gas Station  0.09
4               Supermarket  0.09
5         Martial Arts Dojo  0.09
6                    Market  0.09
7                  Pharmacy  0.09
8       Fried Chicken Joint  0.09
9            Discount Store  0.09
10        Outdoor Sculpture  0.00
11                   Museum  0.00
12              Music Store  0.00
13              Music Venue  0.00
14               Nail Salon  0.00
15  New American Restaurant  0.00
16                    Plaza  0.00
17                Nightclub  0.00
18               Non-Profit  0.00
19             Noodle House  0.00


----Annadale----
                      venue  freq
0              Cocktail Bar   1.0
1               Yoga Studio   0.0
2      Pakistani Restaurant   0.0
3     Outdoors & Recreation   0.0
4      Outdoor Supply Store   0.0
5         Outdoor Sculpture   0.0
6      Other

                       venue  freq
0                        Spa  0.12
1                Pizza Place  0.12
2      Vietnamese Restaurant  0.12
3           Greek Restaurant  0.12
4           Sushi Restaurant  0.12
5             Cosmetics Shop  0.12
6           Asian Restaurant  0.12
7   Mediterranean Restaurant  0.12
8                 Non-Profit  0.00
9       Other Great Outdoors  0.00
10              Optical Shop  0.00
11               Opera House  0.00
12                    Office  0.00
13              Noodle House  0.00
14                 Nightclub  0.00
15      Outdoor Supply Store  0.00
16   New American Restaurant  0.00
17                Nail Salon  0.00
18               Music Venue  0.00
19               Music Store  0.00


----Bedford Park----
                      venue  freq
0               Bus Station   0.5
1        Chinese Restaurant   0.5
2               Yoga Studio   0.0
3              Noodle House   0.0
4      Outdoor Supply Store   0.0
5         Outdoor Sculpture   0.0
6   

                      venue  freq
0           Harbor / Marina  0.33
1                Hobby Shop  0.33
2                   Dog Run  0.33
3     Outdoors & Recreation  0.00
4      Outdoor Supply Store  0.00
5         Outdoor Sculpture  0.00
6      Other Great Outdoors  0.00
7              Optical Shop  0.00
8               Opera House  0.00
9                    Office  0.00
10             Noodle House  0.00
11               Non-Profit  0.00
12     Pakistani Restaurant  0.00
13                Nightclub  0.00
14  New American Restaurant  0.00
15               Nail Salon  0.00
16              Music Venue  0.00
17              Music Store  0.00
18                   Museum  0.00
19            Moving Target  0.00


----Broadway Junction----
                      venue  freq
0             Deli / Bodega  0.14
1                  Bus Stop  0.14
2                     Hotel  0.14
3       Japanese Restaurant  0.14
4        Mexican Restaurant  0.14
5                Food Stand  0.14
6                   

                      venue  freq
0            Ice Cream Shop  0.25
1       Japanese Restaurant  0.25
2            Sandwich Place  0.25
3             Deli / Bodega  0.25
4         Paella Restaurant  0.00
5      Outdoor Supply Store  0.00
6         Outdoor Sculpture  0.00
7      Other Great Outdoors  0.00
8              Optical Shop  0.00
9               Opera House  0.00
10                   Office  0.00
11             Noodle House  0.00
12               Non-Profit  0.00
13                Nightclub  0.00
14  New American Restaurant  0.00
15               Nail Salon  0.00
16              Music Venue  0.00
17              Music Store  0.00
18                   Museum  0.00
19            Moving Target  0.00


----Central Harlem----
                              venue  freq
0                              Café  0.07
1     Vegetarian / Vegan Restaurant  0.07
2   Southern / Soul Food Restaurant  0.07
3              Gym / Fitness Center  0.07
4                    Breakfast Spot  0.07
5        

                            venue  freq
0                   Deli / Bodega  0.25
1                     Coffee Shop  0.25
2          Argentinian Restaurant  0.25
3                  Pilates Studio  0.25
4                     Opera House  0.00
5               Paella Restaurant  0.00
6           Outdoors & Recreation  0.00
7            Outdoor Supply Store  0.00
8               Outdoor Sculpture  0.00
9            Other Great Outdoors  0.00
10                   Optical Shop  0.00
11                   Noodle House  0.00
12                         Office  0.00
13  Paper / Office Supplies Store  0.00
14                     Non-Profit  0.00
15                      Nightclub  0.00
16        New American Restaurant  0.00
17                     Nail Salon  0.00
18                    Music Venue  0.00
19                    Music Store  0.00


----College Point----
                            venue  freq
0              Spanish Restaurant  0.17
1                     Video Store  0.17
2               

...

                      venue  freq
0            Sandwich Place  0.33
1                Shoe Store  0.33
2      Caribbean Restaurant  0.33
3                    Office  0.00
4      Outdoor Supply Store  0.00
5         Outdoor Sculpture  0.00
6      Other Great Outdoors  0.00
7              Optical Shop  0.00
8               Opera House  0.00
9              Noodle House  0.00
10        Paella Restaurant  0.00
11               Non-Profit  0.00
12                Nightclub  0.00
13  New American Restaurant  0.00
14               Nail Salon  0.00
15              Music Venue  0.00
16              Music Store  0.00
17                   Museum  0.00
18    Outdoors & Recreation  0.00
19              Yoga Studio  0.00


----Queensboro Hill----
                            venue  freq
0                Asian Restaurant  0.19
1                          Bakery  0.12
2              Chinese Restaurant  0.12
3                            Bank  0.06
4                      Bagel Shop  0.06
5                   

                      venue  freq
0                      Park   1.0
1               Yoga Studio   0.0
2         Paella Restaurant   0.0
3      Outdoor Supply Store   0.0
4         Outdoor Sculpture   0.0
5      Other Great Outdoors   0.0
6              Optical Shop   0.0
7               Opera House   0.0
8                    Office   0.0
9              Noodle House   0.0
10               Non-Profit   0.0
11                Nightclub   0.0
12  New American Restaurant   0.0
13               Nail Salon   0.0
14              Music Venue   0.0
15              Music Store   0.0
16                   Museum   0.0
17            Moving Target   0.0
18            Movie Theater   0.0
19    Outdoors & Recreation   0.0


----Rockaway Beach----
                      venue  freq
0             Deli / Bodega  0.33
1                     Beach  0.33
2                   Butcher  0.17
3   New American Restaurant  0.17
4               Music Store  0.00
5              Optical Shop  0.00
6      Pakistani Restau

                        venue  freq
0                         Bar  0.13
1                    Creperie  0.04
2            Greek Restaurant  0.04
3                      Lounge  0.04
4                   Pet Store  0.04
5                Burger Joint  0.04
6   Middle Eastern Restaurant  0.04
7                  Bagel Shop  0.04
8          Mexican Restaurant  0.04
9   Latin American Restaurant  0.04
10           Tapas Restaurant  0.04
11                       Park  0.04
12                Pizza Place  0.04
13              Deli / Bodega  0.04
14              Grocery Store  0.04
15                Coffee Shop  0.04
16          Indian Restaurant  0.04
17        American Restaurant  0.04
18       Caribbean Restaurant  0.04
19                        Pub  0.04


----Springfield Gardens----
                      venue  freq
0                Playground  0.33
1          Business Service  0.33
2                Shoe Store  0.33
3               Yoga Studio  0.00
4              Noodle House  0.00
5      Out

                      venue  freq
0                     Hotel  0.75
1                  Wine Bar  0.25
2               Yoga Studio  0.00
3                Non-Profit  0.00
4      Outdoor Supply Store  0.00
5         Outdoor Sculpture  0.00
6      Other Great Outdoors  0.00
7              Optical Shop  0.00
8               Opera House  0.00
9                    Office  0.00
10             Noodle House  0.00
11  New American Restaurant  0.00
12                Nightclub  0.00
13        Paella Restaurant  0.00
14               Nail Salon  0.00
15              Music Venue  0.00
16              Music Store  0.00
17                   Museum  0.00
18            Moving Target  0.00
19            Movie Theater  0.00


----Tribeca----
                            venue  freq
0                             Spa  0.10
1                           Hotel  0.05
2                         Dog Run  0.05
3                    Cycle Studio  0.05
4                     Salad Place  0.05
5                     Coffee

                      venue  freq
0                       Spa   0.5
1               Comedy Club   0.5
2      Pakistani Restaurant   0.0
3     Outdoors & Recreation   0.0
4      Outdoor Supply Store   0.0
5         Outdoor Sculpture   0.0
6      Other Great Outdoors   0.0
7              Optical Shop   0.0
8               Opera House   0.0
9                    Office   0.0
10             Noodle House   0.0
11               Non-Profit   0.0
12                Nightclub   0.0
13  New American Restaurant   0.0
14               Nail Salon   0.0
15              Music Venue   0.0
16              Music Store   0.0
17                   Museum   0.0
18            Moving Target   0.0
19        Paella Restaurant   0.0


----Williamsburg----
                        venue  freq
0                 Pizza Place   0.2
1   Latin American Restaurant   0.2
2                 Coffee Shop   0.1
3                 Wings Joint   0.1
4                         Gym   0.1
5             Bubble Tea Shop   0.1
6          

#### Let's put that into a *pandas* dataframe

First, let's write a function to sort the venues in descending order.

In [135]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [136]:
num_top_venues = 1

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = NY_grouped['Neighborhood']

for ind in np.arange(NY_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(NY_grouped.iloc[ind, :], num_top_venues)

#neighborhoods_venues_sorted.head()


grouped = neighborhoods_venues_sorted.groupby('1st Most Common Venue').count().reset_index()
grouped.sort_values('Neighborhood', ascending=False).head(10).reset_index(drop=True)


#grouped = df.groupby('mygroups').sum().reset_index()
#grouped.sort_values('mygroups', ascending=False)

#row_categories_sorted = row_categories.sort_values(ascending=False)

#neighborhood1 = neighborhoods_venues_sorted.sort_values(by='Neighborhood',ascending=False)
#neighborhood1.head(10) 


1st Most Common Venue  Neighborhood
0         Deli / Bodega            26
1           Pizza Place            16
2            Playground            11
3                  Park             8
4           Bus Station             8
5    Italian Restaurant             8
6                   Bar             7
7         Grocery Store             7
8    Chinese Restaurant             7
9                  Bank             5

<a id='item4'></a>